In [1]:
import pandas as pd
import numpy as np
import funciones

#base de datos con las denuncias

df_paot = pd.read_csv(r"C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\df_paot_con_limpieza.csv", encoding = 'latin')
df_paot[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]] = df_paot[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]].apply(pd.to_datetime, errors = 'coerce')
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_columns', None)

# o tambien probar matches con:

#

C:\Users\samue\AppData\Local\Temp\ipykernel_6436\327134928.py:7: DtypeWarning: Columns (22) have mixed types. Specify dtype option on import or set low_memory=False.
  df_paot = pd.read_csv(r"C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\df_paot_con_limpieza.csv", encoding = 'latin')
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '30/01/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '29/04/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritorio\Ve

In [2]:
from simpledbf import Dbf5

dbf = Dbf5(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\ri_11.dbf')

#base de datos externa, densidad de poblacion
df_pob = dbf.to_dataframe().dropna()


funciones.estandarizacion(df_pob, 'colonia', 'alcaldia')

PyTables is not installed. No support for HDF output.
SQLalchemy is not installed. No support for SQL output.


In [3]:
dbf = Dbf5(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\ue_comerciales_colonia.dbf')

#base de datos externa, densidad de poblacion
df_ue = dbf.to_dataframe().dropna()

funciones.estandarizacion(df_ue, 'nombre', 'alcaldia')


In [4]:
df_victimas = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\analisis_maltrato_animal\data\clean\df_victimas.csv', encoding='utf-8')


In [5]:
df_tianguis = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\analisis_maltrato_animal\data\raw\tianguis\c16cc0f7-8307-4a5f-a2d4-25e83b71faae', encoding='utf-8')

funciones.estandarizacion(df_tianguis,'ALCALDIA','NOMBRE_COL')

funciones.limpiar_encabezados(df_tianguis)

In [6]:
df_maltrato_animal = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\analisis_maltrato_animal\data\clean\df_maltrato_animal_categorizado', encoding='utf-8')
#df_maltrato_animal = df_paot[(df_paot['fecha_de_recepcion'].dt.year >= 2019 )& (df_paot['materia']=='Maltrato Animal')]

#df_maltrato_animal.to_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\analisis_maltrato_animal\data\clean\maltrato_animal_sin_actualizacion')

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\samue\\OneDrive\\Documents\\GitHub\\captain_planet_sammy\\captain-planet\\analisis_maltrato_animal\\data\\clean\\df_maltrato_animal_categorizado'

In [ ]:
def preparacion_enriquecimiento(df_og, alcaldias_og, colonias_og,  id_denuncia_og):
    df_a_enriquecer = df_og.groupby([alcaldias_og,colonias_og]).count().loc[:,[id_denuncia_og]]

    df_a_enriquecer= df_a_enriquecer.rename(columns={id_denuncia_og:'num_denuncias'})
    return df_a_enriquecer


In [ ]:
datos_corr = preparacion_enriquecimiento(df_maltrato_animal, 'alcaldia','colonia','id_denuncia')


In [ ]:
funciones.enriquecimiento(datos_corr, df_pob, 'alcaldia','colonia', ['SUP_COL_M2', 'pob_2010'],['superficie_metros_cuadrados', 'poblacion_2010'], False)
funciones.enriquecimiento(datos_corr, df_ue, 'alcaldia','nombre', ['ue', 'ind','com','serv'],['unidades_economicas','industriales','comerciales','servicios'], False)


In [ ]:
funciones.enriquecimiento(datos_corr, df_victimas,'alcaldiahechos','coloniahechos',['idcarpeta'], ['num_carpetas'], 'conteo')
funciones.enriquecimiento(datos_corr, df_victimas[df_victimas['delito']=='CAMBIO DE USO DE SUELO'], 'alcaldiahechos', 'coloniahechos', ['idcarpeta'], ['num_carpetas_maltrato'], 'conteo')
funciones.enriquecimiento(datos_corr, df_victimas[df_victimas['delito']=='ROBO DE ANIMALES'], 'alcaldiahechos', 'coloniahechos', ['idcarpeta'], ['num_carpetas_robo_animales'], 'conteo')


In [ ]:
funciones.enriquecimiento(datos_corr, df_tianguis, 'alcaldia', 'nombre_col', ['_id'], ['tianguis'],'conteo')

In [ ]:


funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['maltrato_fisico'],['maltrato_fisico'],'suma')
funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['intemperie_o_inmovilidad'],['intemperie_o_inmovilidad'],'suma')
funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['subalimentacion'],['subalimentacion'],'suma')
funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['criadero'],['criadero'],'suma')
funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['rituales'],['rituales'],'suma')
funciones.enriquecimiento(datos_corr, df_maltrato_animal,'alcaldia','colonia',['comercio'],['comercio'],'suma')

In [ ]:
correlaciones = datos_corr.corr()

In [ ]:
import plotly.express as px


fig = px.imshow(correlaciones, text_auto=True)
fig.show()

->checar q lista de colonias vamos a usar !!
-> checar bien streamlit !!
-> armar focos con geopandas
